<img src="pic/ex02.png" width="100%"> <br>

<h1 class="jp-toc-ignore">ICON Training - Hands-on Session</h1>

# Exercise 2: Global Real Data Run

---

The course exercises revisit the topics of the individual tutorial chapters and range from easy tests to the setup of complex forecast simulations.

In this particular exercise you will learn how to 

- **start a global ICON forecast** from DWD analysis data
- **activate a nest** over Europe
- **configure** the ICON **model output namelist**
  - example: creating boundary data for driving a limited area ICON
- make use of **the ICON LOG output**

**Note:** This script is not suited for operational use, it is part of the step-by-step tutorial.
Furthermore, we will omit some of ICON's less important input and output channels here, e.g. the restart files. This exercise focuses on command-line tools and the rudimentary visualization with Python scripts. Professional post-processing and viz tools are beyond the scope of this tutorial.

    
---

## Input Data

---

<figure style="float:right;">
<img src="./pic/ICON_realcase_input_data.png" width="550" alt="alt_text"/>
<figcaption style="text-align:center"><b>Necessary input data for a global ICON-NWP run</b> </figcaption>
</figure>

**Global ICON-NWP** runs require a number of input data, in particular 
<ul>
    <li><b>grid files:</b> coordinates and topological index relations between cells, edges and vertices</li>
    <li><b>external parameter files:</b> time invariant fields such as topography, lake depths or soil type</li>
    <li><b>initial conditions:</b> snapshot of an atmospheric state and soil state from which the model is integrated forward in time</li>
</ul>

This data is already available in the directory `/pool/data/ICON/ICON_training/exercise_realdata`.

On default, ICON expects the input data to be located in the experiment directory (termed `$EXPDIR` in the run scripts).
The run script creates symbolic links in the experiment directory, which point to the input files.

---

## Setup

---

<figure style="float:right;">
<img src="pic/exp_real_R2B6N7_nest_location_zoomout.png" width="420" alt="alt_text"/>
<figcaption style="text-align:center"><b>Two-way nested domain over Europe with 20 km resolution (R2B07)</b> </figcaption>
</figure>

We prepare a **global forecast with 40 km horizontal grid spacing and a 20 km nest over Europe**. More details are given in the table below. 

| Configuration            |   global     |  nest         |
| :---                     | :---         |  :---         |
| mesh size                | 40 km (R2B6) | 20 km (R2B7)  |
| model top height         | 75 km        | 23 km         |
| no. of levels            | 90           | 60            |
| no. of cells (per level) | 327680       | 9376          |
| time step                | 360 s        | 180 s         |
| duration                 | 48h          | (see exercise)|

---

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Setting up the environment I):</b> 
    </br>
    Execute the following cell in order to set some environment variables that will be used during this exercise</a>
</div>

In [ ]:
# base directory for ICON sources and binary:
ICONDIR=/pool/data/ICON/ICON_training/icon/

# directory with input grids and external data:
GRIDDIR=/pool/data/ICON/ICON_training/exercise_realdata/grids
# directory with initial data:
DATADIR=/pool/data/ICON/ICON_training/exercise_realdata/data/ini

# absolute path to directory with plenty of space:
SCRATCHDIR=/scratch/${USER::1}/$USER
EXPDIR=$SCRATCHDIR/exercise_realdata

# absolute path to files needed for radiation
RADDIR=${ICONDIR}/externals/ecrad/data

# path to prepared namelists
NMLDIR=$HOME/icon-training-scripts/exercise_realdata/nml

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Setting up the environment II):</b> 
    </br>
    Execute the cell below, in order to copy/link input data to the experiment directory <code>$EXPDIR</code>: grids, external parameters, initial conditions.</br>
The directory for the experiment will be created, if not already there.</a>
</div>

In [ ]:
if [ ! -d $EXPDIR ]; then
    mkdir -p $EXPDIR
fi
cd ${EXPDIR}

# grid files: link to output directory
ln -sf ${GRIDDIR}/iconR*.nc .
# external parameter files: link to output directory
ln -sf ${GRIDDIR}/extpar*.nc .
# analysis files: link to output directory
ln -sf ${DATADIR}/*.grb .

# Dictionary for the mapping: DWD GRIB2 names <-> ICON internal names
ln -sf ${ICONDIR}/run/ana_varnames_map_file.txt map_file.ana

# For Output: Dictionary for the mapping: names specified in the output nml <-> ICON internal names
ln -sf ${ICONDIR}/run/dict.output.dwd dict.output.dwd

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Sanity check):</b> 
    </br>
    Check the content of the experiment directory <code>$EXPDIR</code> by using, for example, the <code>ls</code> linux command.</a>
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>
    
```
lrwxrwxrwx 1 m300173 mh0287    55 Jul  7 14:52 dict.output.dwd -> /pool/data/ICON/ICON_training/icon//run/dict.output.dwd
lrwxrwxrwx 1 m300173 mh0287    79 Jul  7 14:52 dwdANA_R2B06_DOM01.grb -> /pool/data/ICON/ICON_training/exercise_realdata/data/ini/dwdANA_R2B06_DOM01.grb
lrwxrwxrwx 1 m300173 mh0287    79 Jul  7 14:52 dwdANA_R2B07_DOM02.grb -> /pool/data/ICON/ICON_training/exercise_realdata/data/ini/dwdANA_R2B07_DOM02.grb
lrwxrwxrwx 1 m300173 mh0287    69 Jul  7 14:52 extpar_DOM01.nc -> /pool/data/ICON/ICON_training/exercise_realdata/grids/extpar_DOM01.nc
lrwxrwxrwx 1 m300173 mh0287    69 Jul  7 14:52 extpar_DOM02.nc -> /pool/data/ICON/ICON_training/exercise_realdata/grids/extpar_DOM02.nc
lrwxrwxrwx 1 m300173 mh0287    72 Jul  7 14:52 iconR2B05_DOM00.nc -> /pool/data/ICON/ICON_training/exercise_realdata/grids/iconR2B05_DOM00.nc
lrwxrwxrwx 1 m300173 mh0287    72 Jul  7 14:52 iconR2B06_DOM01.nc -> /pool/data/ICON/ICON_training/exercise_realdata/grids/iconR2B06_DOM01.nc
lrwxrwxrwx 1 m300173 mh0287    72 Jul  7 14:52 iconR2B07_DOM02.nc -> /pool/data/ICON/ICON_training/exercise_realdata/grids/iconR2B07_DOM02.nc
lrwxrwxrwx 1 m300173 mh0287    65 Jul  7 14:52 map_file.ana -> /pool/data/ICON/ICON_training/icon//run/ana_varnames_map_file.txt
```

</details>

###

## Prepare the ICON run (namelists etc.)

### Create the **ICON master namelist**

The start date is
>  2021-07-13T00:00:00  
>  i.e. July 13, 2021.

The forecast time is 
> 48 hours
> 
<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (master namelist):</b></br> 
    Fill in the missing namelist parameters <code>ini_datetime_string</code> and <code>end_datetime_string</code>. See Section 5.1.1 of the 
    <a href="icon_exercise_realdata.ipynb#Further-Reading-and-Resources">ICON tutorial</a> "Basic Settings for Running Real Data Runs" for details . 
</div>

In [ ]:
cat > icon_master.namelist << EOF

! master_nml: ----------------------------------------------------------------
&master_nml
 lrestart                   =                      .FALSE.        ! .TRUE.=current experiment is resumed
/

! master_model_nml: repeated for each model ----------------------------------
&master_model_nml
 model_type                  =                          1         ! identifies which component to run (atmosphere,ocean,...)
 model_name                  =                       "ATM"        ! character string for naming this component.
 model_namelist_filename     =              "NAMELIST_NWP"        ! file name containing the model namelists
 model_min_rank              =                          1         ! start MPI rank for this model
 model_max_rank              =                      65536         ! end MPI rank for this model
 model_inc_rank              =                          1         ! stride of MPI ranks
/

! time_nml: specification of date and time------------------------------------
&time_nml
 ini_datetime_string         =      "??????????????"        ! initial date and time of the simulation
 end_datetime_string         =      "??????????????"        ! end date and time of the simulation
                                                            ! example date: 2001-01-01T01:00:00Z
 dt_restart                  =      1000000.
/

EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>
    
```
&time_nml
ini_datetime_string         =      "2021-07-13T00:00:00Z"  ! initial date and time of the simulation
end_datetime_string         =      "2021-07-15T00:00:00Z"  ! end date and time of the simulation
```

</details>

###  

### Create the **ICON model namelists**

In the following we will build up the ICON namelist `NAMELIST_NWP` step by step. To do so, we use the UNIX `cat` command in order to collect individual namelists into a single file (named `NAMELIST_NWP`). 

- for a complete list of Namelist parameters see [Namelist_overview.pdf](../Namelist_overview.pdf)

**Please make sure that you execute each of the following cells only once!**

Due to the command `cat >> NAMELIST_NWP << EOF` (note the double `>>`), the namelist groups such as `parallel_nml` below will be concatenated each time you execute the cell.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Basic settings):</b> 
    <ul>
        <li> Set the namelist parameters <code>ltestcase</code>, <code>ldynamics</code>, <code>ltransport</code>, and <code>iforcing</code> for a real data NWP run.</br> 
             See Section 5.1.1 ("Basic Settings for Running Real Data Runs") of the tutorial for details.
    </ul>
    <b style="color:#2d4b9b;">Exercise (Activating a nest over Europe):</b> 
    <ul>
        <li> Activate a global R2B6 domain with R2B7 nest by specifying the list of horizontal grids to be used (<code>dynamics_grid_filename</code>).</br> 
             See Section 4.1.2, "Specifying the Computational Domain(s)", of the tutorial.</li>
        <li> In order to save computational resources, the nested domain should have a reduced model top height and comprise only the lowermost 60 vertical levels of the global domain (instead of 90 levels). Please specify <code>num_lev</code> (<code>run_nml</code>) accordingly. </br> 
             See Section 4.1.2, "Specifying the Computational Domain(s)", of the tutorial.</li>
        <li> Specify the grid on which radiation will be computed<code>radiation_grid_filename</code>. Radiation should be computed on a coarser (reduced) grid with half the resolution for both domains.</br> 
             See Section 3.10, "Reduced Radiation Grid", of the tutorial.</li>
    </ul>
    <b>Hint:</b> A prerequisit for calculating radiation on a reduced grid is the namelist setting <code>lredgrid_phys=.TRUE.,.TRUE.</code>, which has already been prepared for you.
</div>

In [ ]:
cat > NAMELIST_NWP << EOF

! run_nml: general switches ---------------------------------------------------
&run_nml
 ltestcase                   =              ?????????????         ! idealized testcase runs
 num_lev                     =              ?????????????         ! number of full levels (atm.) for each domain
 lvert_nest                  =                      .TRUE.        ! vertical nesting
 dtime                       =                        360.        ! timestep in seconds
 ldynamics                   =              ?????????????         ! compute adiabatic dynamic tendencies
 ltransport                  =              ?????????????         ! compute large-scale tracer transport
 ntracer                     =                          5         ! number of advected tracers
 iforcing                    =              ?????????????         ! forcing of dynamics and transport by parameterized processes
                                                                  ! 2: AES physics package
                                                                  ! 3: NWP physics package
 msg_level                   =                         13         ! controls how much printout is written during runtime
 ltimer                      =                      .FALSE.       ! timer for monitoring the runtime of specific routines
 timers_level                =                          1         ! performance timer granularity
 output                      =                       "nml"        ! main switch for enabling/disabling components of the model output
/

! grid_nml: horizontal grid --------------------------------------------------
&grid_nml
 dynamics_grid_filename      =                 ??????????         ! array of the grid filenames for the dycore
 radiation_grid_filename     =                 ??????????         ! grid filename for the radiation model
 lredgrid_phys               =               .TRUE.,.TRUE.        ! .true.=radiation is calculated on a reduced grid
 lfeedback                   =                      .TRUE.        ! specifies if feedback to parent grid is performed
 ifeedback_type              =                          2         ! feedback type (incremental/relaxation-based)
 start_time                  =                     0.,  0.        ! Time when a nested domain starts to be active [s]
 end_time                    =                  0., 86400.        ! Time when a nested domain terminates [s]
 nexlevs_rrg_vnest           =                         14         ! numer of extra model layers for radiation
/

EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
&run_nml
 ltestcase                   =                    .FALSE.         ! idealized testcase runs
 num_lev                     =                     90,60          ! number of full levels (atm.) for each domain
 ldynamics                   =                     .TRUE.         ! compute adiabatic dynamic tendencies
 ltransport                  =                     .TRUE.         ! compute large-scale tracer transport
 iforcing                    =                          3         ! forcing of dynamics and transport by parameterized processes

&grid_nml
 dynamics_grid_filename      = 'iconR2B06_DOM01.nc','iconR2B07_DOM02.nc' ! array of the grid filenames for the dycore
 radiation_grid_filename     =       'iconR2B05_DOM00.nc'         ! grid filename for the radiation model
```

</details>

<br/>

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Asynchronous output):</b> 
    <ul>
        <li> For improved runtime performance, activate <i>asynchronous</i> output by setting the number of dedicated I/O processors (<code>num_io_procs</code>) to a value larger than 0 (e.g. 2).</br>
             See Section 8.2 ("Settings for Parallel Execution") of the tutorial for more details on the asynchronous output module.
    </ul>
</div>

In [ ]:
cat >> NAMELIST_NWP << EOF

! parallel_nml: MPI parallelization -------------------------------------------
&parallel_nml
 nproma                      =                         32         ! loop chunk length
 p_test_run                  =                     .FALSE.        ! .TRUE. means verification run for MPI parallelization
 num_io_procs                =              ?????????????         ! number of I/O processors
 num_restart_procs           =                          0         ! number of restart processors
 iorder_sendrecv             =                          3         ! sequence of MPI send/receive calls
 num_dist_array_replicas     =                         10         ! distributed arrays: no. of replications
 use_omp_input               =                      .TRUE.        ! allows task parallelism for reading atmospheric input data
/

EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
&parallel_nml
num_io_procs                =                         2          ! number of I/O processors
```

</details>

###  

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (External parameter settings):</b>
    <ul>
      <li>Set the appropriate <code>itopo</code> value for real data runs and specify the name of the external parameter file (<code>extpar_filename</code>).</br>
          Rather than specifying a comma-separated list of filenames, you must make use of the keyword <code>&lt;idom&gt;</code>. </br>
          See Section 5.1.1 of the tutorial ("Basic Settings for Running Real Data Runs") for more details on keywords.</li>
    </ul>
    <b>Hint:</b> You will find the external parameter files in your current working directory <code>$EXPDIR</code>.
</div>

In [ ]:
cat >> NAMELIST_NWP << EOF

! extpar_nml: external data --------------------------------------------------
&extpar_nml
 itopo                       =              ?????????????         ! topography (0:analytical)
 itype_lwemiss               =                          2         ! requires updated extpar data
 itype_vegetation_cycle      =                          1         ! specifics for annual cycle of LAI
 extpar_filename             =              ?????????????         ! filename of external parameter input file
 n_iter_smooth_topo          =                        1,1         ! iterations of topography smoother
 hgtdiff_max_smooth_topo     =                   750.,750.        ! see Namelist doc
 pp_sso                      =                          1         ! type of postprocessing for SSO standard deviation
 read_nc_via_cdi             =                      .TRUE.        ! TRUE/FALSE: read NetCDF input data using CDI or parallel NetCDF library
/

EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
&extpar_nml
itopo                       =                          1         ! topography (0:analytical)
extpar_filename             =       'extpar_DOM<idom>.nc'        ! filename of external parameter input file
```
    
</details>

###  

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Model initialization):</b> 
    <ul>
        <li>The model shall be started from an <b>initialized DWD analysis</b>. Set the appropriate initialization mode <code>init_mode</code>.</br>
            See Tutorial Section 5.1.4, "Starting from Initialized DWD Analysis".</li>
        <li>Specify the name (and path) of the initial data (analysis) file by setting the Namelist parameter <code>dwdfg_filename</code> </li>
        <ul>
            <li>Instead of specifying the full name, make use of the keywords <code>&lt;nroot&gt;</code>, <code>&lt;jlev&gt;</code>, <code>&lt;idom&gt;</code>.</br> See Section 5.1.2 of the tutorial for a list of available keywords.</li>
            <li>Hint: Identify the initial data file (analysis) in your current working directory <code>&#36EXPDIR</code>.</br> You can make use of relative or absolute paths.</li>
        </ul>
        <li>Activate surface tiles.</br>
            Please activate 3 dominant land tiles per grid cell by setting <code>ntiles</code> (<code>lnd_nml</code>) appropriately. Since the initial data contain aggregated (cell averaged) surface fields, a tile coldstart must be performed, i.e. each surface tile must be initialized with the same cell averaged value. The corresponding namelist switch is termed <code>ltile_coldstart</code> (see Section 3.8.9, "Land-Soil Model TERRA").</li>
    </ul>
</div>

In [ ]:
cat >> NAMELIST_NWP << EOF

! initicon_nml: specify read-in of initial state ------------------------------
&initicon_nml
 init_mode                  =              ?????????????         ! start from initialized DWD analysis
 dwdfg_filename             =              ?????????????         ! initialized analysis data
 ltile_coldstart            =              ?????????????         ! coldstart for surface tiles
 lp2cintp_sfcana            =                       .TRUE.       ! interpolate surface analysis from global domain onto nest
 ana_varnames_map_file      =                'map_file.ana'      ! dictionary mapping internal names onto GRIB2 shortNames
/
! lnd_nml: land scheme switches -----------------------------------------------
&lnd_nml
 ntiles                      =              ?????????????         ! number of land tiles
 nlev_snow                   =                          3         ! number of snow layers
 lmulti_snow                 =                      .FALSE.       ! .TRUE. for use of multi-layer snow model
 idiag_snowfrac              =                         20         ! type of snow-fraction diagnosis
 lsnowtile                   =                       .TRUE.       ! .TRUE.=consider snow-covered and snow-free separately
 itype_canopy                =                          2         ! Type of canopy parameterization
 itype_root                  =                          2         ! root density distribution
 itype_trvg                  =                          3         ! BATS scheme with add. prog. var. for integrated plant transpiration since sunrise
 itype_evsl                  =                          4         ! type of bare soil evaporation
 itype_heatcond              =                          3         ! type of soil heat conductivity
 itype_lndtbl                =                          4         ! table for associating surface parameters
 itype_snowevap              =                          3         ! Snow evap. in vegetated areas with add. variables for snow age and max. snow height
 cwimax_ml                   =                          5.e-4     ! scaling parameter for maximum interception parameterization
 c_soil                      =                          1.25      ! surface area density of the (evaporative) soil surface
 c_soil_urb                  =                          0.5       ! surface area density of the (evaporative) soil surface, urban areas
 lseaice                     =                      .TRUE.        ! .TRUE. for use of sea-ice model
 llake                       =                      .TRUE.        ! .TRUE. for use of lake model
 lprog_albsi                 =                      .TRUE.        ! sea-ice albedo is computed prognostically
 sstice_mode                 =                          2         ! SST is updated by climatological increments on a daily basis
/

EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
&initicon_nml
init_mode                  =                          7                ! start from initialized DWD analysis
dwdfg_filename             ='./dwdANA_R<nroot>B<jlev>_DOM<idom>.grb'   ! initialized analysis data
ltile_coldstart            =                       .TRUE.              ! coldstart for surface tiles

&lnd_nml
ntiles                     =                           3               ! number of tiles
```

</details>

###  

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Namelist finalization):</b></br> 
    <b>Add additional namelist groups</b> from the file <code>$NMLDIR/NAMELIST_NWP_base</code>, by executing the following cell. 
</div>

In [ ]:
cat $NMLDIR/NAMELIST_NWP_base >> NAMELIST_NWP

###  

The initial conditions file (i.e. here the initialized analysis) is provided via the namelist parameter `dwdfg_filename` `(initicon_nml)`, see Section 5.1.4 "Starting from Initialized DWD Analysis", of the tutorial.

As an exercise you have been asked to set the file name, using the keyword nomenclature.

In the following small exercise, we will try to understand how these keywords work.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Keywords):</b></br> 
    Which of the following filenames would be accepted by the ICON model, given the following keyword nomenclature</br>
    <code>dwdfg_filename = './dwdANA_R&ltnroot&gtB&ltjlev&gt_DOM&ltidom&gt.grb'</code>?
    <ol>
        <li><code>dwdANA_R3B06.grb</code></li>
        <li><code>dwdANA_R2B6_DOM01.grb</code></li>
        <li><code>dwdANA_R9B02_DOM02.grb</code></li>
        <li><code>dwdana_R2B06_DOM01.grb</code></li>
    </ol>
    <b>Hint:</b> See Section 5.1.2, "Starting from Uninitialized DWD Analysis" of the tutorial for keyword definitions.
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

- [ ] `dwdANA_R3B06.grb`: no, "DOM..." missing
- [ ] `dwdANA_R2B6_DOM01.grb`: no, only single digit
- [x] `dwdANA_R9B02_DOM02.grb`: yes
- [ ] `dwdana_R2B06_DOM01.grb`: no on case-sensitive Linux file system

</details>

###  

<table style="border-collapse:collapse; width:100%; font-size: 1em; font-family: var(--jp-content-font-family, 'Segoe UI', Arial, sans-serif);">
  <tr>
    <td style="vertical-align:top; border:none; padding-right:32px;">
      <div class="alert alert-success" style="padding:15px; border-radius:4px;">
        <b style="color:#2d4b9b;">Exercise (One-way versus two-way nesting):</b><br>
        Open a terminal <button data-commandlinker-command="terminal:create-new">Create Terminal</button> and navigate to the experiment directory <code>EXPDIR</code>, where you will find the full model namelist <code>NAMELIST_NWP</code>.<br>
        Have a look at the namelist group <code>grid_nml</code>, to find out about the following nesting details.<br> 
        <ul>
          <li>Is the domain over Europe one-way nested or two-way nested (i.e. is the feedback to the global domain turned on or off)?</li>
          <li>When does the nested domain get activated and deactivated? Please write down the dates.</li> 
        </ul>
        <b>Hint:</b> See Section 5.2, "Starting or Terminating Nested Domains at Runtime" for additional help.
      </div>
    </td>
    <td style="vertical-align:top; border:none; width:50%; text-align:center;">
      <figure style="margin:0;">
        <img src="./pic/nesting_feedback.png" width="600" alt="alt_text"/>
        <figcaption style="text-align:center; font-weight:bold;">
          Parent-child feedback
        </figcaption>
      </figure>
    </td>
  </tr>
</table>


Answer: One-way versus two-way nesting

Answer: Nested domain start and end times

<details>
<summary style="font-size: 1.1em;">Solution</summary>

The domain over Europe is two-way nested. (Incremental) feedback to the global domain is turned on.

```
&grid_nml
 lfeedback                   =                      .TRUE.        ! specifies if feedback to parent grid is performed
```
</br>

The nested domain starts at 2021-07-13T00:00:00 (model start) and terminates after one  day at 2021-07-14T00:00:00.

```
&grid_nml
 start_time                  =                    0.,  0.        ! Time when a nested domain starts to be active [s]
 end_time                    =                 0., 86400.        ! Time when a nested domain terminates [s]
```
</details>

###  

## Running the model and inspecting the output

Execute the following cell, in order to **create the ICON batch job file** (job will **not** be submitted to the HPC cluster)

In [ ]:
cat > $EXPDIR/icon.sbatch << 'EOF'
#!/bin/bash
#SBATCH --job-name=testjob
#SBATCH --partition=compute
#SBATCH --nodes=6
#SBATCH --ntasks-per-node=128
#SBATCH --output=slurm.%j.out
#SBATCH --exclusive
#SBATCH --mem-per-cpu=960
#SBATCH --time=00:20:00

### ENV ###
env
set -xe

unset SLURM_EXPORT_ENV 
unset SLURM_MEM_PER_NODE
unset SBATCH_EXPORT

ulimit -c 0 # limit core file size
ulimit -l unlimited

export SLURM_DIST_PLANESIZE="32"
export OMPI_MCA_btl="self"
export OMPI_MCA_coll="^ml,hcoll"
export OMPI_MCA_io="romio321"
export OMPI_MCA_osc="ucx"
export OMPI_MCA_pml="ucx"
export UCX_HANDLE_ERRORS="bt"
export UCX_TLS="shm,dc_mlx5,dc_x,self"
export UCX_UNIFIED_MODE="y"
export MALLOC_TRIM_THRESHOLD_="-1"
export OMPI_MCA_pml_ucx_opal_mem_hooks=1

module load eccodes

export ECCODES_DEFINITION_PATH=/pool/data/ICON/ICON_training/eccodes/definitions.edzw-2.27.0-1:$ECCODES_DEFINITION_PATH
export OMP_NUM_THREADS=1

# path to model binary, including the executable:
MODEL=$ICONDIR/build/bin/icon

srun -l --cpu_bind=verbose --hint=nomultithread --distribution=block:cyclic $MODEL

EOF

### Running the ICON model

Submit the job to the HPC cluster, using the Slurm command `sbatch`.

In [ ]:
export ICONDIR=$ICONDIR
cd $EXPDIR && sbatch --account=$SLURM_JOB_ACCOUNT icon.sbatch

### Checking the job status

Check the job status via `squeue`.

### Inspecting the Model Output

After the job has finished, inspect the model output. Take a look at the output files in <code>$EXPDIR</code>.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Horizontal output grid):</b>
    </br>
    One of the files contains output on the native ICON grid, the other one contains the output on a regular lat/lon grid. <br/>
    How can you identify which file is which (apart from the obvious file names that we have chosen)? Use <code>cdo sinfov</code> to identify the relevant metadata.
    </br></br>
    <b>Hint:</b> You might have to load the environment modules <code>cdo</code>
    
</div>

Answer: native

Answer: lat/lon

<details>
<summary style="font-size: 1.1em;">Solution</summary>

Answer: native  
output on native grid : NWP\_DOM01\_ML\_0001.nc (grid coordinates = 'unstructured')

Answer: lat/lon  
output on lat/lon grid: NWP\_lonlat\_DOM01\_ML\_0001.nc (grid coordinates = 'lonlat')

```
cd $EXPDIR
module load cdo

set +o xtrace
cdo sinfov NWP_DOM01_ML_0001.nc  | grep  -B0 -A1 "Grid coordinates"
cdo sinfov NWP_lonlat_DOM01_ML_0001.nc  | grep  -B0 -A1 "Grid coordinates"
```
</details>

###  

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Vertical output grid):</b></br>
    For the output on regular lat/lon grid, use <code>cdo sinfov</code> to identify the type of atmospheric vertical output grid.
    <ul>
      <li>model level (ML)</li>
      <li>pressure level (PL)</li>
    <li>height level (HL)</li>
    </ul>  
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>
    
SAMPLE SOLUTION: Type of atm. vertical output grid : ML = "model levels" (CDO depicts `generalized_height`)

```
cd $EXPDIR
module load cdo
cdo sinfov NWP_lonlat_DOM01_ML_0001.nc | grep "Vertical coordinates" -B0 -A1
```
</details>

###  

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Visualization):</b></br> 
    Visualize the 2m temperature, integrated water vapor, gusts at 10m, and total precipitation using the script <a href=scripts/icon_exercise_realdata_plot01.ipynb>icon_exercise_realdata_plot01.ipynb</a>.</br>
    If you like, you can look into other fields and timesteps as well, or make use of <code>ncview</code> for visualizing the interpolated lat-lon output.
</div>

###

## Time-stepping

<table style="border-collapse:collapse; width:100%;">
  <tr>
    <td style="vertical-align:top; border:none; padding-right:32px;">
      <p>
        This exercise focuses on aspects of the ICON time-stepping scheme, explained in Section 3.7.1, "<b>ICON Time-Stepping</b>".
      </p>
    </td>
    <td style="vertical-align:top; border:none; width:55%; text-align:center;">
      <figure style="margin:0;">
        <img src="./pic/time_stepping.png" width="720" alt="alt_text"/>
        <figcaption style="text-align:center; font-weight:bold;">
          ICON internal time stepping
        </figcaption>
      </figure>
    </td>
  </tr>
</table>


<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Time-stepping):</b>
    <br>
    Compute the <i>dynamics</i> time step <b>Δτ</b> from the specification of the physics time step <b>Δt</b> (<code>dtime</code>) and the number of dynamics substeps <code>ndyn_substeps (nonhydrostatic_nml)</code>.
    <br><br>
    <b>Hint:</b> Have a look at the model Namelist <code>$EXPDIR/NAMELIST_NWP</code>
</div>


<details>
<summary style="font-size: 1.1em;">Solution</summary>
   
Answer: 360s/5 = 72s

</details>

###  

The timestep is proportional to the effective mesh size $\overline{\Delta x}$ of the horizontal ICON grid. 

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Now take a look at Equation (3.52) on page 91 of the Tutorial handbook and calculate an estimate for the maximum dynamics time step Δτ<sub>max</sub>  which is allowed for the horizontal grid spacing at hand. <br/>
    Compare this to the time step used: Did we make a reasonable choice?
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>
    
Answer: 
The effective mesh size of a global grid can be estimated as <p>
$
\overline{\Delta x} \approx 5050/(n\,2^k) \quad [\mathrm{km}]\,.
$

**Example Python code**
```
python3 - << EOF
n = 2 # grid_root
k = 6 # grid_level

mesh_size = 5050/(n * 2**k) # [km]
print(f"mesh size: {mesh_size} [km]")

delta_tau_max = 1.8 * mesh_size
print(f"delta tau_max: {delta_tau_max} [s]");
EOF
```
<br>

**Result**<br>
$\Delta \tau_{max} = 1.8 \cdot 10^{-3} \cdot 39453.125 ~[s] \approx 71 ~[s] $

</details>

###  

## Optional: Appending your own output namelist

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Output namelists for LAM initialization and forcing):</b></br>
    We will add an additional output namelist, in order to learn about its most important options.</br>
    As an example, we will write a particular set of output fields, which is suitable for driving a limited area run (so called <b>forcing or boundary data</b>).</br>
    Fill in the missing parameters below:<br/>
    Forcing data should be written
    <ul>
        <li>in GRIB2 format</li>
        <li>for the EU-nest only</li>
        <li>2-hourly, beginning at model start until 24 hours forecast time</li>
        <li>with one output step per file</li>
        <li>on the native (triangular) grid</li>
        <li>into the subdirectory `lam_forcing` of your output directory, using the filename prefix `forcing`. If the subdirectory does not exist, please create.</li>
        <li>containing model level output for <code>U</code>, <code>V</code>, <code>W</code>, <code>PRES</code>, <code>TEMP</code>, <code>QV</code>, <code>QC</code>, <code>QI</code>, <code>QR</code>, <code>QS</code>, <code>HHL</code>.</li>
    </ul>
    <b>Hint:</b> See Section 7.1 ("Settings for the Model Output") of the ICON tutorial for additional details regarding output namelists.
</div>

In [ ]:
cat >> NAMELIST_NWP << EOF

!----------------------------------------------------------------------------
! output_nml: writing boundary data for LAM                             ;----
!----------------------------------------------------------------------------
&output_nml
 filetype                    =              ?????????????         ! output format: GRIB2 or NETCDFv2
 dom                         =              ?????????????         ! write output only for EU-nest
 output_bounds               =              ?????????????         ! output: start, end, increment in s
 steps_per_file              =              ?????????????         ! number of output steps in one output file
 remap                       =              ?????????????         ! (no)remap to regular lat/lon grid (0 or 1)
 output_grid                 =                     .FALSE.        ! flag whether grid information is added to output.
 output_filename             =              ?????????????         ! file name base
 filename_format             = '<output_filename>_<levtype>_<datetime2>' ! full file format
 mode                        =                          1         ! 1: forecast mode (relative t-axis), 2: climate mode (absolute t-axis)
 !
 ml_varlist                  =              ?????????????         ! output fields on model levels
/

EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
cat >> NAMELIST_NWP << EOF

!----------------------------------------------------------------------------
! output_nml: LAM exercise;  writing boundary data for LAM              ;----
!----------------------------------------------------------------------------
&output_nml
 filetype                    =                          2         ! output format: GRIB2 or NETCDFv2
 dom                         =                          2         ! write output only for EU-nest
 output_bounds               =          0., 86400., 7200.         ! output: start, end, increment in s
 steps_per_file              =                          1         ! number of output steps in one output file
 remap                       =                          0         ! (no)remap to regular lat/lon grid (0 or 1)
 output_grid                 =                     .FALSE.        ! flag whether grid information is added to output.
 output_filename             =     './lam_forcing/forcing'        ! file name base
 filename_format             = '<output_filename>_<levtype>_<datetime2>' ! full file format
 mode                        =                          1         ! 1: forecast mode (relative t-axis), 2: climate mode (absolute t-axis)
 !
 ml_varlist                  = 'U','V','W','PRES','TEMP','QV','QC','QI','QR','QS','HHL'  ! output fields on model levels
/

EOF
```

</details>

###

Then, create the additional output directory:

In [ ]:
mkdir -p $EXPDIR/lam_forcing

Submit the batch job.

In [ ]:
export ICONDIR=$ICONDIR
cd $EXPDIR && sbatch --account=$SLURM_JOB_ACCOUNT icon.sbatch

Check the job status via `squeue`.

###

Check the correctness of your output files. You should find **13 forcing data files** in your output directory `lam_forcing`.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Check output files):</b></br> 
    In your Linux terminal, export the following environment variable
    <p>
     <code>export ECCODES_DEFINITION_PATH=/pool/data/ICON/ICON_training/eccodes/definitions.edzw-2.27.0-1:$ECCODES_DEFINITION_PATH</code>
    </p>
    and apply the following command to the last forcing data file:
    <p>
    <code>cdo sinfov data-file.grb > data-file.sinfov</code>
    </p>
    Compare with the reference output below to see whether your output namelist is correct.
</div>


```
   File format : GRIB2
    -1 : Institut Source   T Steptype Levels Num    Points Num Dtype : Parameter name
     1 : DWD      unknown  v instant      60   1      9376   1  P16  : U             
     2 : DWD      unknown  v instant      60   1      9376   1  P16  : V             
     3 : DWD      unknown  v instant      61   2      9376   1  P16  : W             
     4 : DWD      unknown  v instant      60   1      9376   1  P16  : P             
     5 : DWD      unknown  v instant      60   1      9376   1  P16  : T             
     6 : DWD      unknown  v instant      60   1      9376   1  P16  : QV            
     7 : DWD      unknown  v instant      60   1      9376   1  P16  : QC            
     8 : DWD      unknown  v instant      60   1      9376   1  P16  : QI            
     9 : DWD      unknown  v instant      60   1      9376   1  P16  : QR            
    10 : DWD      unknown  v instant      60   1      9376   1  P16  : QS            
    11 : DWD      unknown  v instant      61   3      9376   1  P16  : HHL           
   Grid coordinates :
     1 : unstructured             : points=9376
                             grid : number=101  position=1
                             uuid : 7f1e5eb3-fc61-a692-b99f-830dab7e2440
   Vertical coordinates :
     1 : generalized_height       : levels=60
                           height : 1 to 60 by 1 
                           bounds : 1-2 to 60-61 by 1 
                            zaxis : number=0
                             uuid : baebf431-dfd5-542e-cb76-8394de703140
     2 : generalized_height       : levels=61
                           height : 1 to 61 by 1 
                            zaxis : number=0
                             uuid : baebf431-dfd5-542e-cb76-8394de703140
     3 : generalized_height       : levels=61
                           height : 1 to 61 by 1 
                           bounds : 1-0 to 61-0 by 1 
                            zaxis : number=0
                             uuid : baebf431-dfd5-542e-cb76-8394de703140
         typeOfSecondFixedSurface : 101
   Time coordinate :
                             time : 1 step
     RefTime =  2021-07-13 00:00:00  Units = minutes  Calendar = proleptic_gregorian
  YYYY-MM-DD hh:mm:ss  YYYY-MM-DD hh:mm:ss  YYYY-MM-DD hh:mm:ss  YYYY-MM-DD hh:mm:ss
  2021-07-14 00:00:00
```

###

## Excursion: The ICON LOG output

<figure style="float:right;">
<img src="./pic/ICON_log_file_screenshot.png" width="570" alt="alt_text"/>
<figcaption style="text-align:center"><b>The ICON LOG file</b> </figcaption>
</figure>

During model integration, ICON writes various information to the `stderr` output stream (which serves as an unbuffered substitute for `stdout`). This information is collected by the batch queuing system in a text file often referred to as 'the ICON log file'. 
The name of the log file is defined in the ICON batch script header (see `#SBATCH --output`). In our exercises it is named `slurm.XXX.out`, and 
stored in the output directory `$EXPDIR`.

The amount of information that is printed and stored in the LOG file depends on the verbosity level, which is set in the ICON namelist 
(see the parameter `msg_level` in the namelist `run_nml`).

The **log file contains** various information, such as 
- **information about the model setup**
  - like control output of various subroutines and functions
  - the chosen input fields and grids 
  - output dates
  - ...
- **domain specific information** for each integration time step
  - date and time of each time step
  - global max/min of the normal horizontal and vertical velocity (`vn` and `w`)
  - domain average of the surface pressure tendency $\frac{\mathrm{d}p_s}{\mathrm{d}t}$
  - trigger dates of physical parameterizations

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (The ICON log output):</b> 
    <ul>
      <li>In your Linux terminal, navigate to your experiment directory <code>$EXPDIR</code> and open an existing ICON log file.</li>
      <li>Try to identify the above mentioned domain specific information for an arbitrary integration time step.</li>
      <li>Do you have an idea why there are multiple messages of the form <code>MAXABS VN, W in domain ...</code> for each time step?
    </ul>
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>
    
Answer:

Each line of the form `MAXABS VN, W in domain ...` corresponds to a single integration step of the *dynamical core*. Remember that ICON performs a substepping of the dynamical core with respect to the physics, which means that the dynamical core is called multiple (usually 5) times per physics time step.

</details>

###

### The surface pressure tendency

The **domain averaged surface pressure tendendency** output

$|\large \frac{\mathrm{d}p_s}{\mathrm{d}t}| = \frac{1}{A}\sum_{i}\left(\sum_{k}|-g\nabla_{h}\cdot(\rho v_{h})\,\Delta z_{k}|\right)\Delta a_{i} \,,\quad \text{in Pa/s}$


in your log file can be seen as a measure of the gravity wave activity in your simulation. The tendency includes contributions from 'meteorological' inertia-gravity waves, but also spurious/artificial waves that emerge e.g. from imbalances in the initial conditions. The surface pressure tendency is larger the more gravity waves are present in the forecast. Therefore, it can be used to monitor the noise level of your simulation. See also Section 2.2.1 of the ICON tutorial for more details.  

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Monitoring the noise level of your simulation):</b> <p/>
    In order to visualize the domain averaged surface pressure tendency as a function of time, apply the script <a href="scripts/plot_dpsdt_training.ipynb">scripts/plot_dpsdt_training.ipynb</a> to a log file of your choice.</br>
Describe what you see.
</div>

### Solution

<details>

Answer:

<figure style="float:right;">
<img src="./pic/dpsdt_time_series_nested.png" width="650" alt="alt_text"/>
<figcaption style="text-align:center"><b>Surface pressure tendency</b> </figcaption>
</figure>

- The plot exhibits a high, but rapidly decaying noise level during the first couple of minutes of the model run. The initial noise emerges from spurious imbalances in the initial conditions.

</details>

###  

---

<h2 class="jp-toc-ignore"> <b style="color:#2d4b9b;"><b style="color:#2d4b9b;"> Congratulations! You have successfully completed Exercise 2.</b></h2>

---

## Further Reading and Resources

- ICON Tutorial, Ch. 5: <a href="https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html">https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html</a>
  <br/>A new <b>draft version</b> of the ICON Tutorial is available here: <a href="https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html">https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html</a>. It is currently being finalized and will be published soon.
- Parallelization was not covered in this tutorial exercise. For details, however, there is an optional exercise, see the Jupyter notebook <a href="icon_exercise_parallelization.ipynb"> <pre>icon_exercise_parallelization.ipynb</pre></a>

---

*Author info: Deutscher Wetterdienst (DWD) 2025 ::  icon@dwd.de. For a full list of contributors, see CONTRIBUTING in the root directory. License info: see LICENSE file.*